### Lecture 4: Homework

Today we gonna learn how to choose between ML models, based on data type. Your task would be to predict **the edibility of a mushroom** based on sample descriptions (binary classification problem)

The **tricky part here is that 95% of the features are of categorical type.**
<br>That's the one where we would **(usually)  prefer tree-based algorithms over linear methods**

Although this dataset was originally contributed to the UCI Machine Learning repository nearly 30 years ago, mushroom hunting (otherwise known as "shrooming") is enjoying new peaks in popularity. Learn which features spell certain death and which are most palatable in this dataset of mushroom characteristics. And how certain can your model be?

This dataset includes descriptions of hypothetical samples corresponding to 23 species of gilled mushrooms in the Agaricus and Lepiota Family Mushroom drawn from The Audubon Society Field Guide to North American Mushrooms (1981). Each species is identified as definitely edible, definitely poisonous, or of unknown edibility and not recommended. This latter class was combined with the poisonous one. The Guide clearly states that there is no simple rule for determining the edibility of a mushroom; no rule like "leaflets three, let it be'' for Poisonous Oak and Ivy.

More information can be found [here](https://www.kaggle.com/uciml/mushroom-classification/data)

Please find below correspondent [google form](https://docs.google.com/forms/d/e/1FAIpQLScmKfUApMlcD81u9UZxM7xG3vJiEJHrPrG-3b0i_jyPEDijgQ/viewform) to submit your answers

In [8]:
# library import
import pandas as pd
import numpy as np
from os.path import join as pjoin
pd.options.display.max_columns = 50
pd.options.display.max_colwidth = 100

# preprocessing / validation
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from sklearn.model_selection import (
    train_test_split, StratifiedKFold, cross_val_score, GridSearchCV
)
# ML models
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression

# metrics
from sklearn.metrics import classification_report, f1_score

In [109]:
# read data
DATA_DIR = '../data'
df_train = pd.read_csv(pjoin(DATA_DIR, '4-mushrooms-train.csv'), engine='c')
df_test = pd.read_csv(pjoin(DATA_DIR, '4-mushrooms-test.csv'), engine='c')
print(df_train.shape, df_test.shape)

(6499, 23) (1625, 22)


In [110]:
# let's see what data looks like
df_train.head()

target cap_shape cap_surface cap_color  bruises     odor gill_attachment  \
0       0    convex       scaly     brown  bruises  pungent            free   
1       1      flat     fibrous      gray  bruises     none            free   
2       0      flat      smooth     brown       no     none        attached   
3       1    convex     fibrous      gray  bruises     none            free   
4       0   knobbed      smooth     brown       no     foul            free   

  gill_spacing gill_size gill_color stalk_shape stalk_root  \
0        close    narrow      white   enlarging      equal   
1        close     broad      brown    tapering    bulbous   
2        close     broad     orange   enlarging    missing   
3        close     broad      brown    tapering    bulbous   
4        close    narrow       buff    tapering    missing   

  stalk_surface_above_ring stalk_surface_below_ring stalk_color_above_ring  \
0                   smooth                   smooth                  white   
1                   smooth                   smooth                  white   
2                   smooth                   smooth                 orange   
3                   smooth                   smooth                  white   
4                    silky                   smooth                   pink   

  stalk_color_below_ring veil_type veil_color ring_number   ring_type  \
0                  white   partial      white         one     pendant   
1                  white   partial      white         one     pendant   
2                 orange   partial     orange         one     pendant   
3                  white   partial      white         one     pendant   
4                   pink   partial      white         one  evanescent   

  spore_print_color population habitat  
0             brown  scattered   urban  
1             brown    several   woods  
2             brown    several  leaves  
3             black   solitary   woods  
4             white    several   paths

In [111]:
# for convenient calculations, let us merge train with test
df = pd.concat([df_train, df_test], axis=0)
# add column for filtering train/test
df['is_train'] = True
df.loc[df.target.isnull(), 'is_train'] = False
# check shapes
print(df.shape)
# check labels
df.is_train.value_counts()

(8124, 24)


True     6499
False    1625
Name: is_train, dtype: int64

In [112]:
##Swap columns here
columns = list(df)
columns[-4],columns[0]= columns[0],columns[-4]
df = df.ix[:,columns]

/Users/mac/anaconda3/lib/python3.5/site-packages/ipykernel_launcher.py:4: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  after removing the cwd from sys.path.


In [44]:
import pandas_profiling
report=pandas_profiling.ProfileReport(df_train)  ##I'm using df_train here because on the whole dataset it throws an error about the deprecation or something... I do this just to get a glance at the range of features 

In [43]:
report
## Veil_type seems to be redundant feature

### Task 1. Which feature has the highest amount of unique values? (joint dataset)


In [113]:
unique_vals = np.argsort([len(df[column].value_counts()) for column in df.columns])
column_max = unique_vals[-1]    

In [114]:
# 
# 
# ---------------------------------------------------------------
most_diversive = df.iloc[:,column_max].name
# ---------------------------------------------------------------

print(most_diversive)

gill_color


### Task 2
**As a preparation, one would spend up to 15-30 minutes on exploratory data analysis (EDA)** - make sure you understand how features are distributed in train/test, what they look like, are they ordinal/binary/categorical before moving further
<br>While doing it, please answer the questions

#### 2.1 Are there any features, obviously redundant to train on? If yes - what are they and why it's better to remove them?

According to pandas_profiling - "veil-type" is a constant feature

In [115]:
print(df.shape)
# your code/hardcoded list goes here
# ---------------------------------------------------------------
redundant_columns = [
    "veil_type"
]
# ---------------------------------------------------------------
# lets drop these columns from joint dataset
df.drop(redundant_columns, axis=1,inplace=True)
print(df.shape)

(8124, 24)
(8124, 23)


####  2.2 How many features (excluding target variable and train/test indexing columns) are:
- categorical (more than 2 unique values, no explicit ordering)
- ordinal (more than 2 unique values, explicit ordering)
- binary (2 unique values, doesn't matter whether it has ordering or is "yes/no" styled) 

All features are categorical

In [138]:
# your code goes here
# ---------------------------------------------------------------
ordinal_cols = sorted([
   "ring_number",
    
])
binary_cols = sorted([
    "bruises",
    "gill_attachment",
    "gill_size",    
    "gill_spacing",
    "stalk_shape",
    
])
categorical_cols = sorted(set(df.columns) - set(binary_cols) - set(ordinal_cols))
# ---------------------------------------------------------------
print('categorical: {}\nordinal: {}\nbinary: {}'.format(
    len(categorical_cols), len(ordinal_cols), len(binary_cols)))

categorical: 17
ordinal: 1
binary: 5


In [122]:
# To be used in training, data must be properly encoded
from collections import defaultdict

# function to encode categorical data
def __encode_categorical(df_list, cat_cols):
    # initialize placeholder
    d = defaultdict(LabelEncoder)
    # fit and encode train/test,
    codes = pd.concat(
        [df[cat_cols] for df in df_list],
        axis=0
    )
    codes.fillna('').apply(
        lambda x: d[x.name].fit(x)
    ),
    # transform encodings to train/test etc
    for df in df_list:
        df[cat_cols] = df[cat_cols].fillna('').apply(
            lambda x: d[x.name].transform(x))


# label encode data (categorical + binary)
__encode_categorical(df_list=[df], cat_cols=categorical_cols+binary_cols)

# make sure you encode the only ordinal column in correct order
df[ordinal_cols[0]] = df[ordinal_cols[0]].map({'none': 0, 'one': 1, 'two': 2})

# define useful feature columns to be used for training
# (union of all columns discussed above)
columns_to_use = ordinal_cols + binary_cols + categorical_cols

In [124]:
df.dropna(inplace=True)

### Task 3. Prepare cross-validation strategy and perform comparison of 2 baseline models (linear vs tree-based)

### =====================================================
#### Briefly about Validation / Cross-Validation

Learning the parameters of a prediction function and testing it on the same data is a methodological mistake: a model that would just repeat the labels of the samples that it has just seen would have a perfect score but **would fail to predict anything useful on yet-unseen data. This situation is called overfitting**. 
<br>To avoid it, it is common practice when performing a (supervised) machine learning experiment to hold out part of the available data as a test set ```X_test, y_test```. 
<br>Note that the word “experiment” is not intended to denote academic use only, because even in commercial settings machine learning usually starts out experimentally.

When evaluating different settings (“hyperparameters”) for estimators, **there is still a risk of overfitting on the test set** because the parameters can be tweaked until the estimator performs optimally. 
<br>This way, knowledge about the test set can “leak” into the model and evaluation metrics no longer report on generalization performance. 
<br>To solve this problem, yet another part of the dataset can be held out as a so-called “validation set”: training proceeds on the training set, after which evaluation is done on the validation set, and when the experiment seems to be successful, final evaluation can be done on the test set.

However, by partitioning the available data into three sets, **we drastically reduce the number of samples which can be used for learning the model, and the results can depend on a particular random choice for the pair of (train, validation) sets.**

A solution to this problem is a procedure called **cross-validation (CV for short). A test set should still be held out for final evaluation, but the validation set is no longer needed when doing CV**. In the basic approach, called k-fold CV, the training set is split into k smaller sets (other approaches are described below, but generally follow the same principles). The following procedure is followed for each of the k “folds”:

- A model is trained using k-1 of the folds as training data;
- the resulting model is validated on the remaining part of the data 
<br>(i.e., it is used as a test set to compute a performance measure such as accuracy).
        
<img src="https://hsto.org/files/b1d/706/e6c/b1d706e6c9df49c297b6152878a2d03f.png"/ style="width:75%">

The performance measure reported by k-fold cross-validation **is then the average of the values computed in the loop**. 
<br>This approach can be computationally expensive, but does not waste too much data (as it is the case when fixing an arbitrary test set), which is a major advantage in problem such as inverse inference where the number of samples is very small.


Some classification problems can **exhibit a large imbalance in the distribution of the target classes: for instance there could be several times more negative samples than positive samples**. 
<br>In such cases it is recommended to use **stratified sampling** as implemented in sklearn's StratifiedKFold and StratifiedShuffleSplit to ensure that relative class frequencies is approximately preserved in each train and validation fold.

More details about different cross-validation strategies, implemented in sklearn, can be found [here](http://scikit-learn.org/stable/modules/cross_validation.html)
### =====================================================

Prepare KFold with 5 splits, stratified by target variable, shuffled, with fixed random_state = 42
<br>**Don't forget to filter by column 'is_train'!**
<br>Fit models on subset of features: [columns_to_use]

In [125]:
from sklearn.cross_validation import train_test_split
df_train,df_test = train_test_split(df,test_size=0.2)

In [133]:
from os import cpu_count

n_jobs = max(cpu_count()-1, 1)
print(n_jobs)
# your code goes here
# ---------------------------------------------------------------
# cross-validation iterator
kf = 5
# xtrain, ytrain, DataFrame-like
xtrain = df_train[df_train.columns[1:]]
ytrain = df_train[df_train.columns[0]]
# ---------------------------------------------------------------

# create Decision Tree with default params, max_depth=4, random_state=42
dt = DecisionTreeClassifier(max_depth=3, random_state=42)

# estimate its f1-score with cross-validation (cross_val_score)
# your code goes here
# ---------------------------------------------------------------
scores_dt = cross_val_score(
    estimator=dt,
    X=xtrain, # ...
    y=ytrain, # ...
    scoring='f1', # ...
    cv=kf, # cross-validation strategy
    n_jobs=n_jobs
).mean()
print('DT scoring: {:.4f}'.format(scores_dt))
# ---------------------------------------------------------------


# create Logistic Regression with default params, random_state=42
lr = LogisticRegression(
  random_state=42
)

# estimate its f1-score with cross-validation
# your code goes here
# ---------------------------------------------------------------
scores_lr = cross_val_score(
    estimator=lr,
    X=xtrain, # ...
    y=ytrain, # ...
    scoring='f1',
    cv=kf,
    n_jobs=n_jobs
).mean()
print('LR scoring: {:.4f}'.format(scores_lr))

3
DT scoring: 0.9013
LR scoring: 0.8940


Why is a score of Linear Regression lower than correspondent one of DT?
1. Is everything OK with the data format for linear models? (revision of 2 previous lectures). 
1. If not, what else you should do to use the data appropriately for linear models?
1. Why didn't point 1. affect Decision Tree performance?

**Answer** I assume scaling is an important factor here. In our case, I would opt for one-hot encoding for the linear models.
DTs are not affected by scaling, so they manage to have better results. 

### Task 4. Now it's time to do some hyperparam tuning
Perform suitable hyperparam tuning using created above cross-validation strategy
<br>Main parameters to perform grid-search for:
- max_depth (1,2,...None)
- min_samples_leaf (1,2,...)
- criterion (gini, entropy)
- weight (none, balanced)
- max_features (sqrt(features), 50%, 75%, all of them, ...)
- other params available, see documentation

So - use your fantasy for filling-in abovementioned lists

You should receive **a gain of 0.01 in f1-score or higher**
<br>(current benchmark = +0.0268 gain)

In [127]:
%%time
# your code goes here
# ---------------------------------------------------------------
# create base model (DT, random state = 42)
estimator = DecisionTreeClassifier()

# create parameter grid
# http://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html
params = {
    "max_depth" : list(range(2,14,2)),
    "min_samples_leaf" : list(range(1,20,3)),
    "criterion" : ["gini","entropy"],
    "max_features" : ["auto","log2",0.2,0.5,0.8,None],
    "min_samples_split":list(range(2,10,2)),
    "class_weight" : ["balanced",None]
}

# create grid search object
gs = GridSearchCV(
    estimator=estimator,  # base model
    param_grid=params,  # params grid to search within
    cv=kf,  # cross-validation strategy
    error_score=1,  # warnings only
    scoring='f1',  # f1-score
    # thread count, the higher count - the faster
    n_jobs=n_jobs,
    verbose=2,  # messages about performed actions
)

# perform grid search on TRAIN dataset ('is_train' filtering)
gs.fit(
    X=xtrain, # ...
    y=ytrain, # ...
)
# -------------------------------------------------------------
# extract best score on cross-validation
best_score = gs.best_score_
# extract the estimator (DT) with best params on cross-validation
best_dt = gs.best_estimator_
# check gain in f1-score
print('f1-score best: {:.4f}, +{:.4f} better than baseline'.format(
    best_score, (best_score - scores_dt))
)

Fitting 5 folds for each of 4032 candidates, totalling 20160 fits
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2 
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2 
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2, total=   0.1s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=1, class_weight=balanced, min_samples_split=2, total=   0.1s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=

[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=7, class_weight=balanced, min_samples_split=2 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=4, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV]

[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=7, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=6 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=4, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=6 
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=4 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=6, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=6 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=10, class_weight=balanced, min_samples_split=6, total=   0.

[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=13, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=13, class_weight=balanced, min_samples_split=8 
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=16, class_weight=balanced, min_samples_split=2 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=16, class_weight=balanced, min_samples_split=2, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=16, class_weight=balanced, min_samples_split=2 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=13, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=16, class_weight=balanced, min_samples_split=2, total=   0.0s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=16, class_weight=balanced, min_samples_spli

[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=4 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=6, total=   0.0s
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=6 
[CV] max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=8 
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=4, total=   0.0s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_split=8, total=   0.0s
[CV]  max_depth=2, criterion=gini, max_features=auto, min_samples_leaf=19, class_weight=balanced, min_samples_spli

...

[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=4, total=   0.0s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=6 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=4, total=   0.1s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=4 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=6, total=   0.0s
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=6, total=   0.1s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split=8 
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=10, class_weight=None, min_samples_split

[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2, total=   0.0s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=4 
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2, total=   0.0s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=4, total=   0.0s
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=16, class_weight=None, min_samples_split=2, total=   0

[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=8, total=   0.1s
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=6, total=   0.1s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=8 
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=6 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=8, total=   0.1s
[CV] max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=8 
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_split=6, total=   0.0s
[CV]  max_depth=12, criterion=entropy, max_features=None, min_samples_leaf=19, class_weight=None, min_samples_spli

[Parallel(n_jobs=3)]: Done 20160 out of 20160 | elapsed:  7.8min finished


f1-score best: 0.9294, +0.0108 better than baseline
CPU times: user 58.4 s, sys: 19.8 s, total: 1min 18s
Wall time: 7min 50s


In [130]:
# take a look on the best model, compare with the baseline
best_dt

DecisionTreeClassifier(class_weight='balanced', criterion='gini',
            max_depth=10, max_features=0.5, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=7, min_samples_split=8,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [131]:
best_score

0.9294441444646938

In [134]:
# check performance on holdout dataset, unseen before (filter 'is_train' == False)

# your code goes here
# ---------------------------------------------------------------
# appropriate df_test data subset from 'df' dataframe
xtest =  df_test[df_test.columns[1:]]

# fit baseline model 'dt' on xtrain, ytrain (because it's not fitted yet)
dt.fit(xtrain, ytrain)
# ---------------------------------------------------------------

# baseline model
y_true = df_test[df_test.columns[0]]
y_pred_baseline = dt.predict(xtest)

print('Base on train:   {:.4f}\nBase on holdout: {:.4f}\ndiff: {:.4f}'.format(
    scores_dt, 
    f1_score(y_true, y_pred_baseline),
    scores_dt - f1_score(y_true, y_pred_baseline)
))

# best model
y_pred_best = best_dt.predict(xtest)

print('\nBest on train:   {:.4f}\nBest on holdout: {:.4f}\ndiff: {:.4f}'.format(
    best_score, 
    f1_score(y_true, y_pred_best),
    best_score - f1_score(y_true, y_pred_best)
))

Base on train:   0.9013
Base on holdout: 0.8921
diff: 0.0092

Best on train:   0.9294
Best on holdout: 0.9206
diff: 0.0089


Now you can see that 
<br>**absolute values of f1-score is higher and distance between train|holdout is lower** <br>for **best model** in comparison to **baseline**

**Bonus question**:

Consider two possibilities:
- (a) you have trained **one best** (on cross-validation) Decision Tree
- (b) you randomly choose 25 subsets of 70% of training data, fits "overfitted" (max_depth=None) Decision Trees on it - each of them performs slightly worse than Tree in (a), and then average predicted results over all 25 models (overfitted trees)

**Which one of them would most likely give the best results on hold-out dataset? What makes you think that way?**

In 1907, the statistician Sir Francis Galton was visiting s country fair in England, at which a contest was being held 
to guess the dressed weight of an ox was on exhibit. There were 800 guesses, and, while the individual guesses varied widely,
both the mean and the median came out within 1% of the ox's true weight. This principle applies to predictive models as well: averaging of multiple models - an *ensemble* of models - turns to be **more accurate** than just selecting one model. 

So I'd most probably opt for the option **B**